[Day 13](https://adventofcode.com/2019/day/13) puzzle input is an IntCode program (mine is [here](puzzle_input/day13.txt)) which represents a game similar to arkanoid/breakout, and outputs a sequence of commands which can be interpreted to draw a game state. Part 1 involves initializing the game and counting the number of "block" tiles that are on screen. Part 2 involves actually playing the game until you break all the blocks and finding your score.

In [1]:
opcode_add = 1
opcode_mul = 2
opcode_read = 3
opcode_write = 4
opcode_jump_true = 5
opcode_jump_false = 6
opcode_lt = 7
opcode_eq = 8
opcode_rebase = 9

opcode_terminate = 99

mode_position = 0
mode_immediate = 1
mode_relative = 2

class IntCodeCpu:
    def __init__(self, memory_image):
        self.memory = [ x for x in memory_image ] # copy memory image, in case it's reused
        self.stalled = True
        self.input_buffer = None
        self.output_buffer = None
        self.pc = 0
        self.initialise_opcodes()
        self.offset = 0
        self.done = False
        
    def start(self, input_buffer, output_buffer, noun=None, verb=None):
        self.input_buffer = input_buffer
        self.output_buffer = output_buffer

        if noun:
            self.memory[1] = noun
        if verb:
            self.memory[2] = verb
           
        return self.run()
            
            
    def run(self):
        instr = self.memory[self.pc]
        self.stalled = False

        while int(instr) != opcode_terminate and not self.stalled:
            (op, modes) = self.decode_instr(instr)
            self.pc = op(modes)
            instr = self.memory[self.pc]

        return self.memory[0]

    #-HELPERS-----------------------------
    def try_pop_mode(self, modes):
        if len(modes) == 0:
            return 0
    
        return modes.pop()
    
    def resize_memory(self, target_addr):
        self.memory += ([0] * (1 + target_addr - len(self.memory)))
    
    #-DECODE-INSTRUCTIONS-----------------
    def initialise_opcodes(self):
        self.opcodes = {
            opcode_add: self.op_add,
            opcode_mul: self.op_mul,
            opcode_read: self.op_read,
            opcode_write: self.op_write,
            opcode_jump_true: self.op_jump_true,
            opcode_jump_false: self.op_jump_false,
            opcode_lt: self.op_lt,
            opcode_eq: self.op_eq,
            opcode_rebase: self.op_rebase
        }    
    
    def decode_instr(self, instr):
        instr = str(instr)
        opcode = self.decode_op(instr)
        modes = self.decode_modes(instr)

        if not (opcode in self.opcodes):
            raise Exception(f"Invalid opcode {opcode}")

        return (self.opcodes[opcode], modes)    
    
    def decode_op(self, instr):
        if len(instr) > 2:
            return int(instr[-2:])
        return int(instr)
    
    def decode_modes(self, instr):
        if len(instr) > 2:
            return [ int(d) for d in instr[:-2]]
        return []
    
    #-MICRO-OPS---------------------------
    def uop_read(self, value, mode):
        if mode == mode_position:
            if value >= len(self.memory):
                self.resize_memory(value)        

            return int(self.memory[value])

        elif mode == mode_relative:
            if self.offset + value >= len(self.memory):
                self.resize_memory(self.offset + value)     

            return int(self.memory[self.offset + value])

        elif mode == mode_immediate:
            return int(value)

        else:
            raise Exception("UNKNOWN MODE")

    def uop_write(self, dst, value, mode):
        if mode == mode_position:
            if dst >= len(self.memory):
                self.resize_memory(dst)
            self.memory[dst] = value

        elif mode == mode_relative:
            if self.offset + dst >= len(self.memory):
                self.resize_memory(self.offset + dst)     

            self.memory[self.offset + dst] = value

        elif mode == mode_immediate:
            raise Exception(f"cannot write {value} to literal {dst}")


    def uop_cond_jump(self, modes, cond):
        param_mode = self.try_pop_mode(modes)
        param_raw = int(self.memory[self.pc + 1])
        param = self.uop_read(param_raw, param_mode)

        dest_mode = self.try_pop_mode(modes)
        dest_raw = int(self.memory[self.pc + 2])
        dest = self.uop_read(dest_raw, dest_mode)

        if cond(param):
            return dest

        return self.pc + 3

    def uop_cmp(self, modes, cmp):

        param0_mode = self.try_pop_mode(modes)
        param0_raw = int(self.memory[self.pc + 1])
        param0 = self.uop_read(param0_raw, param0_mode)

        param1_mode = self.try_pop_mode(modes)
        param1_raw = int(self.memory[self.pc + 2])
        param1 = self.uop_read(param1_raw, param1_mode)

        dest_mode = self.try_pop_mode(modes)
        dest = int(self.memory[self.pc + 3])

        if cmp(param0, param1):
            self.uop_write(dest, 1, dest_mode)
        else:
            self.uop_write(dest, 0, dest_mode)

        return self.pc + 4
        
    
    #-OPCODES-----------------------------
    def op_add(self, modes):
        arg0_mode = self.try_pop_mode(modes)
        arg1_mode = self.try_pop_mode(modes)
        dest_mode = self.try_pop_mode(modes)

        arg0_raw = int(self.memory[self.pc + 1])
        arg1_raw = int(self.memory[self.pc + 2])
        dest = int(self.memory[self.pc + 3])

        arg0 = self.uop_read(arg0_raw, arg0_mode)
        arg1 = self.uop_read(arg1_raw, arg1_mode)

        self.uop_write(dest, str(int(arg0) + int(arg1)), dest_mode)
        return self.pc + 4

    def op_mul(self, modes):
        arg0_mode = self.try_pop_mode(modes)
        arg1_mode = self.try_pop_mode(modes)
        dest_mode = self.try_pop_mode(modes)

        arg0_raw = int(self.memory[self.pc + 1])
        arg1_raw = int(self.memory[self.pc + 2])
        dest = int(self.memory[self.pc + 3])

        arg0 = self.uop_read(arg0_raw, arg0_mode)
        arg1 = self.uop_read(arg1_raw, arg1_mode)

        self.uop_write(dest, str(int(arg0) * int(arg1)), dest_mode)    
        return self.pc + 4


    def op_read(self, modes):
        dest_mode = self.try_pop_mode(modes)
        dest = int(self.memory[self.pc + 1])
        
        # if the input buffer is empty, we should "stall" and 
        # resume later
        if not self.input_buffer:
            self.stalled = True
            return self.pc
        
        val = self.input_buffer.pop()

        self.uop_write(dest, str(val), dest_mode)

        return self.pc + 2

    def op_write(self, modes):
        src_mode = self.try_pop_mode(modes)
        src_raw = int(self.memory[self.pc + 1])
        src = self.uop_read(src_raw, src_mode)

        self.output_buffer.append(src)

        return self.pc + 2

    def op_jump_true(self, modes):
        return self.uop_cond_jump(modes, lambda x: x != 0)


    def op_jump_false(self, modes):
        return self.uop_cond_jump(modes, lambda x: x == 0)

    def op_lt(self, modes):
        return self.uop_cmp(modes, lambda x, y: x < y)

    def op_eq(self, modes):
        return self.uop_cmp(modes, lambda x, y: x == y)

    def op_rebase(self, modes):    
        param_mode = self.try_pop_mode(modes)
        param_raw = int(self.memory[self.pc + 1])
        param = self.uop_read(param_raw, param_mode)

        self.offset += param

        return self.pc + 2

In [7]:
# 0 is an empty tile. No game object appears in this tile.
# 1 is a wall tile. Walls are indestructible barriers.
# 2 is a block tile. Blocks can be broken by the ball.
# 3 is a horizontal paddle tile. The paddle is indestructible.
# 4 is a ball tile. The ball moves diagonally and bounces off objects.

tile_none = -1
tile_empty = 0
tile_wall = 1
tile_block = 2
tile_paddle = 3
tile_ball = 4

tiles = {
    tile_none: " ",
    tile_empty: ".",
    tile_wall: "#",
    tile_block: "=",
    tile_paddle: "_",
    tile_ball: "*"
}

code = open("puzzle_input/day13.txt", "r").read().strip().split(",")

def parse_game_draw_instructions(raw_instructions):
    
    assert 0 < len(raw_instructions)
    assert 0 == len(raw_instructions) % 3
    
    instructions = []
    
    while raw_instructions:
        x = raw_instructions.pop(0)
        y = raw_instructions.pop(0)
        tile = raw_instructions.pop(0)
        
        instructions.append([x, y, tile])
    
    return instructions

def find_block_tiles():
    
    cpu = IntCodeCpu(code)
    input_buffer = []
    output_buffer = []   
    cpu.start(input_buffer, output_buffer)
    instructions = parse_game_draw_instructions(cpu.output_buffer)
        
    return len([ 1 for x, y, tile_id in instructions if tile_id == tile_block])

print(find_block_tiles())

420


In [8]:
def generate_screen(x=40, y=23):
    screen = []
    for row in range(y + 1):
        screen.append([ tile_none ] * (x + 1))
    return screen

class AsciiPrinter:
    def __init__(self):
        self.screen = generate_screen()
        
    def plot(self, x, y, tile):
        self.screen[y][x] = tile


def render_game(output_buffer, printer):
    tiles_to_draw = parse_game_draw_instructions(output_buffer)

    score = ""
    ball_position = None
    paddle_position = None

    for tile_detail in tiles_to_draw:
        x_str, y_str, tile_str = tile_detail
        x = int(x_str)
        y = int(y_str)
        tile = int(tile_str)
        if y > 0 and x >= 0:
            printer.plot(x, y, tile)

            if tile == tile_ball:
                ball_position = (x, y)
            
            if tile == tile_paddle:
                paddle_position = (x, y)

        elif x == -1 and y == 0:
            score = tile_str
            
    return (ball_position, paddle_position, score)

def signed_unit(n):
    if n == 0:
        return 0
    
    return int(abs(n)/n)

def run_game():
    cpu = IntCodeCpu(code)

    cpu.memory[0] = 2
    input_buffer = [0]
    output_buffer = []    
    cpu.start(input_buffer, output_buffer)
    
    paddle_pos = None
    screen = AsciiPrinter()
    score = None
    
    while cpu.stalled or cpu.output_buffer:
        ball_pos, maybe_paddle_pos, score = render_game(cpu.output_buffer, screen)
        
        if not ball_pos:
            break
            
        ball_x, ball_y = ball_pos
        if maybe_paddle_pos:
            paddle_pos = maybe_paddle_pos 
        paddle_x, paddle_y = paddle_pos
            
        difference = ball_x - paddle_x
        
        cpu.input_buffer.append(signed_unit(difference))
        cpu.run()
    
    print(score)
        
run_game()

21651
